# Chat with pdf file 

In [1]:
# 建议将 PDF 文件保存在 Google Drive 上

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [6]:
# 在 Google Drive 上的工作目录
WORK_DIR = "/content/drive/MyDrive/ChatGPT/Notebooks/ChatPDF/"
# env 文件名称，里面存储 OPENAI API KEY
ENV_FILE = ".env"
# 处理处理的原文件
SRC_FILE = "jianshang.pdf"
# 缓存的向量 index 文件
INDEX_FILE = SRC_FILE + ".index"

In [3]:
%%capture
# update or install the necessary libraries
!pip install --upgrade llama_index
!pip install --upgrade langchain
!pip install --upgrade python-dotenv


In [4]:
import logging
import sys

logging.basicConfig(stream=sys.stdout, level=logging.INFO)
logging.getLogger().addHandler(logging.StreamHandler(stream=sys.stdout))

In [5]:
from llama_index import GPTSimpleVectorIndex, LLMPredictor, PromptHelper
from llama_index.response.notebook_utils import display_response
from llama_index.prompts.prompts import QuestionAnswerPrompt
from langchain.chat_models import ChatOpenAI
from IPython.display import Markdown, display
from langchain.callbacks.base import CallbackManager
from langchain.callbacks.streaming_stdout import StreamingStdOutCallbackHandler

In [7]:
# Load environment variables (OPENAI_API_KEY)

import os
import shutil
from dotenv import load_dotenv

shutil.copyfile(os.path.join(WORK_DIR, ENV_FILE), ".env")

load_dotenv()

# API configuration
OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")

if OPENAI_API_KEY == "":
  raise Exception("Need set OPENAI_API_KEY")

准备 Index 文件，为了避免重复索引，增加缓存




In [8]:
# Load pdf to documents

from pathlib import Path
from llama_index import download_loader

# 中文 PDF 建议使用 CJKPDFReader，英文建议用 PDFReader
# 其他类型文件，请去 https://llamahub.ai/ 寻找合适的 Loader
CJKPDFReader = download_loader("CJKPDFReader")

loader = CJKPDFReader()
index_file = os.path.join(Path(WORK_DIR), Path(INDEX_FILE))

if os.path.exists(index_file) == False:
  documents = loader.load_data(file=os.path.join(Path(WORK_DIR), Path(SRC_FILE)))
  # 默认 chunk_size_limit=4096，缩减 chunk_size 可以有效降低 Token 使用，但是会导致最终提供给 GPT 的上下文变少，从而影响效果
  index = GPTSimpleVectorIndex(documents, chunk_size_limit=1024)
  index.save_to_disk(index_file)
else:
  index = GPTSimpleVectorIndex.load_from_disk(index_file)


In [64]:
llm_predictor = LLMPredictor(llm=ChatOpenAI(
    # 将 temperature 范围为 0-1，越接近0越具备创造性
    # 典型值：0(arc53/DocsGPT)、0.2(madawei2699/myGPTReader)
    temperature=0,
    model_name="gpt-3.5-turbo",
))


QUESTION_ANSWER_PROMPT_TMPL = (
    "Context information is below. \n"
    "---------------------\n"
    "{context_str}"
    "\n---------------------\n"
    "{query_str}\n"
)

QUESTION_ANSWER_PROMPT_TMPL_2 = """
You are an AI assistant providing helpful advice. You are given the following extracted parts of a long document and a question. Provide a conversational answer based on the context provided.
If you can't find the answer in the context below, just say "Hmm, I'm not sure." Don't try to make up an answer.
If the question is not related to the context, politely respond that you are tuned to only answer questions that are related to the context.

Context information is below.
=========
{context_str}
=========
{query_str}
"""

QUESTION_ANSWER_PROMPT = QuestionAnswerPrompt(QUESTION_ANSWER_PROMPT_TMPL_2)

def chat(query):
  # 当 chunk_size 较小以及问题较为简洁时，回答的语言就不是很好控制，需要在问题增加内容。
  # 目前在 prompt 上进行多次尝试无效，所以直接加到query 上。
  query = query + " 请使用中文回答。"
  result = index.query(
      query,
      llm_predictor=llm_predictor,
      text_qa_template=QUESTION_ANSWER_PROMPT,
      # default: For the given index, “create and refine” an answer by sequentially 
      #   going through each Node; make a separate LLM call per Node. Good for more 
      #   detailed answers.
      # compact: For the given index, “compact” the prompt during each LLM call 
      #   by stuffing as many Node text chunks that can fit within the maximum prompt size. 
      #   If there are too many chunks to stuff in one prompt, “create and refine” an answer 
      #   by going through multiple prompts.
      # tree_summarize: Given a set of Nodes and the query, recursively construct a 
      #   tree and return the root node as the response. Good for summarization purposes.
      response_mode="tree_summarize",
      similarity_top_k=3,
      # mode="default" will a create and refine an answer sequentially through 
      #   the nodes of the list. 
      # mode="embedding" will synthesize an answer by 
      #   fetching the top-k nodes by embedding similarity.
      mode="embedding",
  )
  print(f"Token used: {llm_predictor.last_token_usage}, total used: {llm_predictor.total_tokens_used}")
  return result

# It's not work now, please don't use it.
# Bug: https://github.com/jerryjliu/llama_index/issues/831
def chat_stream(query):
  return index.query(
      query,
      llm_predictor=llm_predictor,
      text_qa_template=QUESTION_ANSWER_PROMPT,
      response_mode="tree_summarize",
      similarity_top_k=3,
      streaming=True,
      mode="embedding",
  )

# response_stream = chat_stream("这本书讲了什么?")
# response_stream.print_response_stream()

In [65]:
resp = chat("这本书讲了什么？")
display_response(resp)

Token used: 4486, total used: 4486


**`Final Response:`** 这本书讲述了商周变革的历史背景和过程，包括周灭商等事件，同时也描绘了许多熟视无睹的场景，让读者可以更好地理解古代中国的思想、信仰、伦理、心态、风俗，以及军事、政治、制度、规则等方面。根据历史学家和教授的评价，这场变革对于华夏文明的意义更深、更远，是中国历史上的重要事件。作者的视角和写法独特，让人耳目一新。对于对古代中国有兴趣的研究者或普通读者来说，是一个很好的探索起点。

---

**`Source Node 1/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8053380387024119<br>**Text:** 在视频和音频节目中，呈现得肯定都是有限的。  说起来，李硕在本书中所描述的，都是我这个在新石器时代至夏 商周考古领域熬至“资深”的学者所耳熟能详的，但他的视角和写法 却又使我耳目一新：他赋予了我...<br>

...

**`Source Node 2/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8041932654562923<br>**Text:** 的支持，其实是心理上的，让我意识到除了祭祀坑里的尸骨，这世界 上还有别的东西。  也许，人不应当凝视深渊；虽然深渊就在那里。    始于一页，抵达世界 Humanities ■ Histor...<br>

---

**`Source Node 3/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.7992281260807114<br>**Text:** 们再次进入幽暗的历史通道前，一窺我们这群人何以如此，何以至今。它将予我们 
鼓励，认识自己，直面未来。

刘苏里万圣书园创办人

-部好的历史著作，不仅要数学家的逻辑，迁要文学家的想象。由此观之...<br>

从这个问题的回答可以看到，当chunk_size 从默认的4096 缩减为 1024 后，因为缺乏上下文，回答不够完整，只有牧野之战的前半部分，之前的回答如下：

在牧野之战开始时，武王率领西土联军面对着数量远超自己的商军。武王的前提是有殷都内部联络人的密约，但局势不断变化，没有商人助战，西土联军将被一边倒地屠杀。武王没有别的选择，他只能相信父亲描述的那位上帝站在自己一边，只要全心信任他，父亲开启的翦商事业就能成功。在战斗开始时，武王一方没有任何章法和战术可言，但商军阵列却突然自行解体，变成了互相砍杀的人群。或许是看到周军义无反顾的冲锋，商军中的密谋者终于鼓起勇气，倒戈杀向纣王中军。接着，西土联军全部投入了混战。后世的周人史诗说，“商庶若化"，即是说，商军队伍就像滚水冲刷的油脂，瞬间溃散，融化。最终，武王率领的西土联军获胜，商王朝终结。

In [66]:
display_response(chat("牧野之战的具体过程是什么？"))

Token used: 4788, total used: 9274


**`Final Response:`** 根据新的上下文，牧野之战的具体过程是：盟军经过六天加急行军，于二月二十一日夜间抵达殷都南郊的牧野，两军都已侦知对方主力的位置，开始连夜整队列阵，准备天亮时一举消灭对手。二十二日甲子凌晨，规模较小的周军首先列队完毕，武王全身盔甲戎装，在阵前宣誓，这便是著名的《尚书•牧誓》。武王手持白旄，高声宣誓：“逖矣，西土之人！”，然后一一点名麾下的盟友、将领、军官，直到“百夫长”，命令他们：“拿起你们的戈，连接好你们的盾牌，立起你们的长矛，现在，我要立誓！”

---

**`Source Node 1/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8107165489961021<br>**Text:** 的宗教思维，知道必须用法术对抗法术，化解纣王自我献祭可能带来 的后果与流言，方法则是表演一次战斗和处斩，展现纣王被俘和被杀 的全过程：周军直入鹿台宫，武王在战车上对着纣王尸体连射三箭, 然后跳下...<br>

...

**`Source Node 2/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8084797679435898<br>**Text:** 事据点可以保持有效联络，一旦某个城邑遭到土著部落威胁，周邻据 点可以尽快参战，战报也可以迅速送到殷都，以便后方组织增援力量。 马拉战车比徒步快三倍以上，这意味着传递战报和命令的时间只需原 来的四...<br>

---

**`Source Node 3/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8057765987066442<br>**Text:** 商人据点，一路向北直指殷都。经过六天加急行军，二月二十一日癸 
丑夜间，盟军抵达殷都南郊的牧野。6这里是商王室蓄养牛羊的草原，
地形平坦，商军集结地的营火已经遥遥在望。此时，两军都已侦知对
方主...<br>

In [68]:
display_response(chat("对商朝人祭文化做一个总结。"))

Token used: 3115, total used: 16625


**`Final Response:`** 商朝人祭文化是一种漫长而顽固的风习，从新石器时代晚期以来算起，已经延续两三千年，商朝更是将其吸收到了王朝制度之中。人祭是商朝的国家宗教，也是商族人的全民宗教，王室成为人祭活动最大的主办者，代表着王权和神权的高度融合。人祭行为不仅出现在宫廷与民间，也被商人带到了各殖民城邑。周公与召公的谈话中，周公认为想要根除上千年的积习，谈何容易。

---

**`Source Node 1/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8775562794009867<br>**Text:** 祭材料。  另外，商人的人祭宗教也和他们的复杂来源有关。灭夏初期，来 自多个文化的人群融合成新兴的“王朝商族”，因此，他们需要构建 一种维系自我认同的宗教文化，而用人献祭是最为明晰和便捷的方式:...<br>

...

**`Source Node 2/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.8724770531874126<br>**Text:** 和统治列族的权柄。  在商人的人祭宗教兴盛之际，王室成为人祭活动最大的主办者。 

这代表着王权和神权的高度融合。比起二里头一夏朝，这是一个新
变化：人祭是商朝的国家宗教，也是商族人的全民宗教。...<br>

---

**`Source Node 3/3`**

**Document ID:** 07dc9745-620b-4274-90eb-0d48f1e9db20<br>**Similarity:** 0.871134373879794<br>**Text:** 其实，此时周公真正关心的问题是商人的人祭文化。商王朝虽然 终结了，但他们用人牲祭祀、奠基和殉葬的传统并没有终止；而且 武王在位期间还曾举行商式献祭，甚至比商人更变本加厉。人祭是 一种漫长而顽固的...<br>